Arenstorf orbit - a stable periodic 3-body orbit where two bodies are
orbiting in a plane, along with a third body of negligible mass (e.g. the Earth, the Moon, and a satellite)

In [ ]:
using OrdinaryDiffEq
using Printf
using PyPlot

In [ ]:
"""
    arenstorf!(dudt, u, z, p, t)

The system of differential equations for the restricted 3-body problem
"""
function arenstorf!(dudt, u, p, t)
    x, y, dxdt, dydt = u
    mu = p
    mu1 = 1.0 - mu
    d(r) = ((x + r)^2 + y^2)^(3/2)
    d1 = d(mu)
    d2 = d(-mu1)
    
    dudt[1] = u[3]
    dudt[2] = u[4]
    dudt[3] = x + 2*dydt  - mu1*(x + mu)/d1 - mu*(x - mu1)/d2
    dudt[4] = y - 2*dxdt  - mu1*y/d1 - mu*y/d2
end

In [ ]:
# Initial conditions and ode parameters
initial_positions =  [0.994,  0.0]
initial_velocities = [0.0,   -2.00158510637908252240537862224]
tspan = (0., 4*17.0652165601579625588917206249)
p = 0.012277471;

In [ ]:
# Solve ODE
prob = ODEProblem(arenstorf!, 
                  vcat(initial_positions, initial_velocities), 
                  tspan, p)
sol = solve(prob, Tsit5(), abstol=1e-15, reltol=1e-15);

In [ ]:
# Visualization parameters
n = 1001             # Number of points
t = range(tspan[1], tspan[2], length=n)
tstep = t[2] - t[1]
f = 0.025             # Fraction of displayed points
pts_disp = round(Int, f*n);  # Number of displayed points

In [ ]:
sol_aren = sol.(t)
x = getindex.(sol_aren, 1)
y = getindex.(sol_aren, 2);

In [ ]:
# Define the plotting limits
x0 = -1.5
x1 = -x0
y0 = -1.5
y1 = -y0

In [ ]:
function snapshot(nt, pts_disp, x0, x1, y0, y1, tspan, tstep)
    nt_start = max(1, nt-pts_disp) 
    axis("square")
    xlim(x0, x1)
    ylim(y0, y1)
    titl = @sprintf("Arensdorf orbit for t = %5.2f .. %5.2f",
                     (nt_start - 1)*tstep + tspan[1],
                     (nt - 1)*tstep + tspan[1])
    title(titl, family="monospace")
    xlabel(L"$x$")
    ylabel(L"$y$")
    grid(true)
    plot(x[nt_start:nt], y[nt_start:nt], color="red", linewidth=0.5,
         label=L"$\mu=0.0122775$")
    plot(x[nt], y[nt], color="red", marker="o", markersize=3.0)
    legend()
end

In [ ]:
fig = figure()
for nt in 1:n
    snapshot(nt, pts_disp, x0, x1, y0, y1, tspan, tstep)
    display(fig)
    sleep(0.01)
    IJulia.clear_output(true) 
    clf()
end